# How to develop a MEC application using the MEC Sandbox HTTP REST API
This tutorial introduces the step by step procedure to create a basic MEC appcation following ETSI MEC standards.
It uses the ETSI MEC Sandbox simulator.



## What is a MEC application

See [The Wiki MEC web site](https://www.etsi.org/technologies/multi-access-edge-computing)


## The basics of developing a MEC application

The developement of a MEC application follows a strict process in order to access the ETSI MEC services and provides valuable services to the customers.
Mainly, this process can be split in several steps:
1. Global initializations (constant, variables...)
2. Create a new instance of a MEC Sandbox (Note that using an existing one could be a solution too (see Annex A)
3. Activate a network scenario in order to access the ETSI MEC services
4. Create a new application identifier
5. Register our MEC application and subscribe to service termination (see MEC 011)
6. Use MEC services in order to provide valuable services to the customers
    6.1. Apply MEC services required subscriptions (e.g. MEC 013 location subscription)
7. Terminate the MEC application
    7.1. Remove MEC services subscriptions
    7.2. Deactivate the current network scenario
    7.3. Delete the instance of the MEC Sandbox
8. Release all the MEC application resources

<b>NOTE:</b> Several application identifier can be created to address several MEC applications

## Use the MEC Sandbox HTTP REST API models and code

The MEC sandbox provides a piece of code (the python sub) that shall be used to develop the MEC application and interact with the MEC Sandbox. This piece of code mainly contains swagger models to serialize/deserialize JSON data structures and HTTP REST API call functions.
The openApi file is availabe [here](https://forge.etsi.org/rep/mec/AdvantEDGE/-/blob/Task2_PoC/go-apps/meep-sandbox-sandbox_api/sandbox_api/swagger.yaml) and the [Swagger editor](https://editor-next.swagger.io/) is used to generate the python sub.

The project architecture is describe [here](images/project_arch.jpg).

The sandbox_api folder contains the python implementation of the HTTP REST API definitions introduced by the openApi [file](https://forge.etsi.org/rep/mec/AdvantEDGE/-/blob/Task2_PoC/go-apps/meep-sandbox-sandbox_api/sandbox_api/swagger.yaml).
The model folder contains the python implementation of the data type definitions introduced by the openApi [file](https://forge.etsi.org/rep/mec/AdvantEDGE/-/blob/Task2_PoC/go-apps/meep-sandbox-sandbox_api/sandbox_api/swagger.yaml).
directory:

Before going to create our MEC application skeleton, the following steps shall be done:
1) Change the working directory (see the project architecture)

In [46]:
import os
os.chdir(os.path.join(os.getcwd(), '../mecapp'))
print(os.getcwd())

/home/yann/dev/jupyter/Sandbox/mecapp


2) Apply the python imports

In [47]:
from __future__ import division # Import floating-point division (1/4=0.25) instead of Euclidian division (1/4=0)

import os
import sys
import re
import logging
import threading
import time
import json
import uuid

import pprint

import six

import swagger_client
from swagger_client.rest import ApiException

from http import HTTPStatus
from http.server import BaseHTTPRequestHandler, HTTPServer

try:
    import urllib3
except ImportError:
    raise ImportError('Swagger python client requires urllib3.')


3) Initialize of the global constants (cell 3)

In [48]:
MEC_SANDBOX_URL     = 'https://mec-platform2.etsi.org'                        # MEC Sandbox host/base URL
MEC_SANDBOX_API_URL = 'https://mec-platform2.etsi.org/sandbox-api/v1'         # MEC Sandbox API host/base URL
PROVIDER            = 'Jupyter2024'                                               # Login provider value - To skip authorization: 'github'
MEC_PLTF            = 'mep1'                                                 # MEC plateform name. Linked to the network scenario
LOGGER_FORMAT       = '%(asctime)s - %(name)s - %(levelname)s - %(message)s' # Logging format
STABLE_TIME_OUT     = 6                                                      # Timer to wait for MEC Sndbox reaches its stable state (K8S pods in running state)
LOGIN_TIMEOUT       = 3 #30                                                     # Timer to wait for user to authorize from GITHUB
LISTENER_IP         = '0.0.0.0'                                              # Listener IPv4 address for notification callback calls
LISTENER_PORT       = 32100                                                  # Listener IPv4 port for notification callback calls
CALLBACK_URI        = "https://yanngarcia.ddns.net/jupyter/sandbox/demo6/v1/"

4) Setup the logger instance and the HTTP REST API (cell 4)

In [49]:
# Initialize the logger
logger = logging.getLogger(__name__)
logger.setLevel(logging.DEBUG)
logging.basicConfig(filename='/tmp/' + time.strftime('%Y%m%d-%H%M%S') + '.log')
l = logging.StreamHandler()
l.setFormatter(logging.Formatter('%(asctime)s - %(name)s - %(levelname)s - %(message)s'))
logger.addHandler(l)

# Setup the HTTP REST API configuration to be used to send request to MEC Sandbox API 
configuration               = swagger_client.Configuration()
configuration.host          = MEC_SANDBOX_API_URL
configuration.verify_ssl    = True
configuration.debug         = True
configuration.logger_format = LOGGER_FORMAT
# Create an instance of ApiClient
sandbox_api = swagger_client.ApiClient(configuration, 'Content-Type', 'application/json')

# Setup the HTTP REST API configuration to be used to send request to MEC Services
configuration1               = swagger_client.Configuration()
configuration1.host          = MEC_SANDBOX_URL
configuration1.verify_ssl    = True
configuration1.debug         = True
configuration1.logger_format = LOGGER_FORMAT
# Create an instance of ApiClient
service_api = swagger_client.ApiClient(configuration1, 'Content-Type', 'application/json')


5) Setup the global variables (cell 5)

In [5]:
# Initialize the global variables
nw_scenarios    = []   # The list of available network scenarios
nw_scenario_idx = -1   # The network scenario idx to activate (deactivate)
app_inst_id     = None # The requested application instance identifier

## Create our first MEC application

The first step to develop a MEC application is to create the application skeleton which contains the minimum steps below:
 
- Login to instanciate a MEC Sandbox
- Logout to delete a existing MEC Sandbox

### First steps: the login/logout

Here is the first squeleton with the following sequence:
- Login
- Print sandbox identifier
- Logout
- Check that logout is effective


#### The login function

To log to the MEC Sandbox, 
the login process is done in two step. In step 1, a user code is requested to GITHUB. In step 2, the user has to enter this user code to https://github.com/login/device and proceed to the authorization.
Please, pay attention to the log '=======================> DO AUTHORIZATION WITH CODE :' which indicates you the user code to use for the authorization.

It uses the HTTP POST request with the URL 'POST /sandbox-sandbox_api/v1/login?provide=github' (see PROVIDER constant).


In [6]:
# Login
def process_login() -> str:
    """
    Authenticate and create a new MEC Sandbox instance.

    :return: The sandbox instance identifier on success, None otherwise
    """ 

    global PROVIDER, logger

    logger.debug('>>> process_login')

    try:
        auth = swagger_client.AuthorizationApi(sandbox_api)
        oauth = auth.login(PROVIDER, async_req = False)
        logger.debug('process_login (step1): oauth: ' + str(oauth))
        # Wait for the MEC Sandbox is running
        logger.debug('=======================> DO AUTHORIZATION WITH CODE : ' + oauth.user_code)
        logger.debug('=======================> DO AUTHORIZATION HERE :      ' + oauth.verification_uri)
        if oauth.verification_uri == "":
            time.sleep(LOGIN_TIMEOUT) # Skip scecurity, wait for a few seconds
        else:
            time.sleep(10 * LOGIN_TIMEOUT) # Wait for Authirization from user side
        namespace = auth.get_namespace(oauth.user_code)
        logger.debug('process_login (step2): result: ' + str(namespace))
        return namespace.sandbox_name
    except ApiException as e:
        logger.error('Exception when calling AuthorizationApi->login: %s\n' % e)

    return None
    # End of function process_login


#### The logout function

It uses the HTTP POST request with the URL 'POST /sandbox-sandbox_api/v1/logout?sandbox_name={sandbox_name}'.


In [7]:
# Logout
def process_logout(sandbox: str) -> int:
    """
    Delete the specified MEC Sandbox instance.

    :param sandbox: The MEC Sandbox to delete
    :return: 0 on success, -1 otherwise
    """

    global logger

    logger.debug('>>> process_logout: sandbox=' + sandbox)

    try:
        auth = swagger_client.AuthorizationApi(sandbox_api)
        result = auth.logout(sandbox, async_req = False)  # noqa: E501
        return 0
    except ApiException as e:
        logger.error('Exception when calling AuthorizationApi->logout: %s\n' % e)
    return -1
    # End of function process_logout


Now, let put in action our Login/Logout functions:

In [ ]:
def process_main():
    """
    This is the skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Logout
        - Check that logout is effective
    This skeleton will be the bas of the next sprint in order to achieve a full implementation of a MEC application
    """ 

    global logger

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        return

    # Print sandbox identifier
    logger.info('Sandbox created: ' + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug('To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A)')
  
    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Second step: Retrieve the list of network scenarios

Let's go futhur and see how we can retrieve the list of the network scenarios available in order to activate one of them and access the MEC services exposed such as MEC 013 or MEC 030.

The sequence will be:
- Login
- Print sandbox identifier
- Print available network scenarios
- Logout
- Check that logout is effective

The login and logout functions are described in cell 3 and 4.

To retrieve the list of the network scenarios, let's create a new function called 'get_network_scenarios'. It uses the HTTP GET request with the URL '/sandbox-sandbox_api/v1/sandboxNetworkScenarios?sandbox_name={sandbox_name}'.

In [8]:
def get_network_scenarios(sandbox: str) -> list:
    """
    Retrieve the list of the available network scenarios.

    :param sandbox: The MEC Sandbox instance to use
    :return: The list of the available network scenarios on success, None otherwise
    """

    global PROVIDER, logger, configuration

    logger.debug('>>> get_network_scenarios: sandbox=' + sandbox)

    try:
        nw = swagger_client.SandboxNetworkScenariosApi(sandbox_api)
        result = nw.sandbox_network_scenarios_get(sandbox, async_req = False)  # noqa: E501
        logger.debug('get_network_scenarios: result: ' + str(result))
        return result
    except ApiException as e:
        logger.error('Exception when calling SandboxNetworkScenariosApi->sandbox_network_scenarios_get: %s\n' % e)

    return None
    # End of function get_network_scenarios


Putting everything together:

In [ ]:
def process_main():
    """
    This is the first sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Logout
        - Check that logout is effective
    """ 
    global logger, nw_scenarios 

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error('Failed to instanciate a MEC Sandbox')
        return

    # Print sandbox identifier
    logger.info('Sandbox created: ' + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error('Failed to retrieve the list of network scenarios')
    elif len(nw_scenarios) != 0:
        logger.info('nw_scenarios: %s', str(type(nw_scenarios[0])))
        logger.info('nw_scenarios: %s', str(nw_scenarios))
    else:
        logger.info('nw_scenarios: No scenario available')

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug('To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A)')
  
    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Third step: Activate and deactivate a network scenario

Having a list of network scenarion, the next step is to actvate (and deactivate) a network scenario. This step is mandatory to create a new application instance id and access the MEC services.

In this section, we will arbitrary activate the network scenario called '4g-5g-macro-v2x', which is at the index 0 of the nw_scenarios. 

In [9]:
def select_network_scenario_based_on_criteria(criterias_list: list) -> int:
    """
    Select the network scenario to activate based of the provided list of criterias.

    :param criterias_list: The list of criterias to select the correct network scenario
    :return: 0 on success, -1 otherwise
    """
    return 0 # The index of the '4g-5g-macro-v2x' network scenario - Hard coded

#### The activate function

The process to activate a scenario is based on an HTTP POST request with the URL '/sandboxNetworkScenarios/{sandbox_name}?network_scenario_id={network_scenario_id}'.


In [10]:
def activate_network_scenario(sandbox: str) -> int:
    """
    Activate the specified network scenario.

    :param sandbox: The MEC Sandbox instance to use
    :return: 0 on success, -1 otherwise
    """

    global logger, configuration, nw_scenarios, nw_scenario_idx

    logger.debug('>>> activate_network_scenario: ' + sandbox)

    nw_scenario_idx = select_network_scenario_based_on_criteria([])
    if nw_scenario_idx == -1:
        logger.error('activate_network_scenario: Failed to select a network scenarion')
        return -1

    try:
        nw = swagger_client.SandboxNetworkScenariosApi(sandbox_api)
        nw.sandbox_network_scenario_post(sandbox, nw_scenarios[nw_scenario_idx].id, async_req = False)  # noqa: E501
        return 0
    except ApiException as e:
        logger.error('Exception when calling SandboxNetworkScenariosApi->activate_network_scenario: %s\n' % e)

    return -1
    # End of function activate_network_scenario


#### The deactivate function

The process to deactivate a scenario is based on an HTTP DELETE request with the URL '/sandboxNetworkScenarios/{sandbox_name}?network_scenario_id={network_scenario_id}'.


In [11]:
def deactivate_network_scenario(sandbox: str) -> int:
    """
    Deactivate the current network scenario.

    :param sandbox: The MEC Sandbox instance to use
    :return: 0 on success, -1 otherwise
    """

    global MEC_SANDBOX_API_URL, logger, configuration, nw_scenarios, nw_scenario_idx

    logger.debug('>>> deactivate_network_scenario: ' + sandbox)

    try:
        nw = swagger_client.SandboxNetworkScenariosApi(sandbox_api)
        nw.sandbox_network_scenario_delete(sandbox, nw_scenarios[nw_scenario_idx].id, async_req = False)  # noqa: E501
        return 0
    except ApiException as e:
        logger.error('Exception when calling SandboxNetworkScenariosApi->deactivate_network_scenario: %s\n' % e)

    return -1
    # End of function deactivate_network_scenario


Now, it is time to create the second iteration of our MEC application.

The sequence is the following:
- Login
- Print sandbox identifier
- Print available network scenarios
- Activate a network scenario
- Check that the network scenario is activated and the MEC services are running
- Deactivate a network scenario
- Logout
- Check that logout is effective



In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Check that the network scenario is activated and the MEC services are running
        - Deactivate a network scenario
        - Logout
        - Check that logout is effective
    """ 
    global logger, nw_scenarios 

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error('Failed to instanciate a MEC Sandbox')
        return

    # Print sandbox identifier
    logger.info('Sandbox created: ' + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error('Failed to retrieve the list of network scenarios')
    elif len(nw_scenarios) != 0:
        logger.info('nw_scenarios: %s', str(type(nw_scenarios[0])))
        logger.info('nw_scenarios: %s', str(nw_scenarios))
        # Wait for the MEC Sandbox is running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running
    else:
        logger.info('nw_scenarios: No scenario available')

    # Activate a network scenario based on a list of criterias (hard coded!!!)
    if activate_network_scenario(sandbox) == -1:
        logger.error('Failed to activate network scenario')
    else:
        logger.info('Network scenario activated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are running
        time.sleep(2 * STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Check that the network scenario is activated and the MEC services are running 
    logger.info('To check that the network scenario is activated, verify on the MEC Sandbox server that the MEC services are running (kubectl get pods -A)')
    time.sleep(30) # Sleep for 30 seconds

    # Deactivate a network scenario based on a list of criterias (hard coded!!!)
    if deactivate_network_scenario(sandbox) == -1:
        logger.error('Failed to deactivate network scenario')
    else:
        logger.info('Network scenario deactivated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are terminated
        time.sleep(2 * STABLE_TIME_OUT)

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug('To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A)')
  
    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Fourth step: Create and delete an appliction instance id

To enable our MEC application to be part of the activated network scenario, we need to request the MEC sandbox to create a new application instance identifier. Our MEC application will use this identifier to register to the MEC Sandbox according to MEC 011.

#### The appliction instance id creation function



In [12]:
def request_application_instance_id(sandbox: str) -> swagger_client.models.ApplicationInfo:
    """
    """

    global MEC_PLTF, logger, configuration

    logger.debug('>>> request_application_instance_id: ' + sandbox)

    # Create a instance of our MEC application
    a = swagger_client.models.ApplicationInfo(id=str(uuid.uuid4()), name='JupyterMecApp', node_name=MEC_PLTF, type='USER')  # noqa: E501
    print(a)
    
    try:
        nw = swagger_client.SandboxAppInstancesApi(sandbox_api)
        result = nw.sandbox_app_instances_post(a, sandbox, async_req = False)  # noqa: E501
        logger.debug('request_application_instance_id: result: ' + str(result))
        return result
    except ApiException as e:
        logger.error('Exception when calling SandboxAppInstancesApi->sandbox_app_instances_post: %s\n' % e)

    return None
    # End of function request_application_instance_id

#### The appliction instance id deletion function

In [13]:
def delete_application_instance_id(sandbox: str, id: str) -> int:
    """
    """

    global logger, configuration

    logger.debug('>>> delete_application_instance_id: ' + sandbox)
    logger.debug('>>> delete_application_instance_id: ' + id)

    try:
        nw = swagger_client.SandboxAppInstancesApi(sandbox_api)
        result = nw.sandbox_app_instances_delete(sandbox, id, async_req = False)  # noqa: E501
        return result
    except ApiException as e:
        logger.error('Exception when calling SandboxAppInstancesApi->sandbox_app_instances_delete: %s\n' % e)

    return -1
    # End of function deletet_application_instance_id

#### Getting the list of applications

In [14]:
def get_applications_list(sandbox: str) -> list:
    """
    """

    global MEC_SANDBOX_API_URL, logger, configuration

    logger.debug('>>> get_applications_list: ' + sandbox)

    try:
        nw = swagger_client.SandboxAppInstancesApi(sandbox_api)
        result = nw.sandbox_app_instances_get(sandbox, async_req = False)  # noqa: E501
        logger.debug('get_applications_list: result: ' + str(result))
        return result
    except ApiException as e:
        logger.error('Exception when calling SandboxAppInstancesApi->get_applications_list: %s\n' % e)

    return None    
    # End of function delete_application_instance_id

It is time now to create the our third iteration of our MEC application.

The sequence is the following:
- Login
- Print sandbox identifier
- Print available network scenarios
- Activate a network scenario
- Request for a new application instance identifier
- Retrieve the list of the applications instance identifier
- Check the demo application is present in the list of applications
- Delete our application instance identifier
- Deactivate a network scenario
- Logout
- Check that logout is effective


In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Request for a new application instance identifier
        - Retrieve the list of the applications instance identifier
        - Check the demo application is present in the list of applications
        - Deactivate a network scenario
        - Logout
        - Check that logout is effective
    """ 
    global logger, nw_scenarios

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error('Failed to instanciate a MEC Sandbox')
        return

    # Print sandbox identifier
    logger.info('Sandbox created: ' + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error('Failed to retrieve the list of network scenarios')
    elif len(nw_scenarios) != 0:
        logger.info('nw_scenarios: %s', str(type(nw_scenarios[0])))
        logger.info('nw_scenarios: %s', str(nw_scenarios))
        # Wait for the MEC Sandbox is running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running
    else:
        logger.info('nw_scenarios: No scenario available')

    # Activate a network scenario based on a list of criterias (hard coded!!!)
    if activate_network_scenario(sandbox) == -1:
        logger.error('Failed to activate network scenario')
    else:
        logger.info('Network scenario activated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are running
        time.sleep(2 * STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Request for a new application instance identifier
    app_inst_id = request_application_instance_id(sandbox)
    if app_inst_id == None:
        logger.error('Failed to request an application instance identifier')
    else:
        logger.info('app_inst_id: %s', str(type(app_inst_id)))
        logger.info('app_inst_id: %s', str(app_inst_id))

    # Check the demo application is present in the list of applications
    app_list = get_applications_list(sandbox)
    if app_list is None:
        logger.error('Failed to request the list of applications')
    else:
        logger.info('app_list: %s', str(type(app_list)))
        logger.info('app_list: %s', str(app_list))
        # Check if our application is present in the list of applications
        found = False
        for item in app_list:
            if item.id == app_inst_id.id:
                found = True
                break
        if not found:
            logger.error('Failed to retrieve our application instance identifier')

    # Delete the application instance identifier
    if delete_application_instance_id(sandbox, app_inst_id.id) == -1:
        logger.error('Failed to delete the application instance identifier')
    else:
        logger.info('app_inst_id deleted: ' + app_inst_id.id)

    # Deactivate a network scenario based on a list of criterias (hard coded!!!)
    if deactivate_network_scenario(sandbox) == -1:
        logger.error('Failed to deactivate network scenario')
    else:
        logger.info('Network scenario deactivated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are terminated
        time.sleep(2 * STABLE_TIME_OUT)

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug('To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A)')
  
    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


## MEC Registration and the READY confirmation

Having an application instance identifier allows us to register with the MEC Sandbox and interact with it (e.g. to send service queries, to subscribe to events and to recieve notifications...).

The standard MEC 011 Clause 5.2.2 MEC application start-up describes the start up process. Basically, our MEC application has to:
1. Indicates that it is running by sending a Confirm Ready message
2. Retrieve the list of MEC services 

To do so, a MEC application needs to be able to send requests but also to receive notifications (POST requests) and to reply to them.

### Fifth step: Send the READY confirmation

Sending READY confirmation is described by MEC 011 Clause 5.2.2 MEC application start-up.


In [15]:
def send_ready_confirmation(sandbox_name: str, app_inst_id: swagger_client.models.application_info.ApplicationInfo) -> int:
    global MEC_PLTF, logger

    logger.debug('>>> send_ready_confirmation: ' + app_inst_id.id)
    try:
        url = '/{sandbox_name}/{mec_pltf}/mec_app_support/v2/applications/{app_inst_id}/confirm_ready'
        logger.debug('send_ready_confirmation: url: ' + url)
        path_params = {}
        path_params['sandbox_name'] = sandbox_name
        path_params['mec_pltf'] = MEC_PLTF
        path_params['app_inst_id'] = app_inst_id.id
        header_params = {}
        # HTTP header `Accept`
        header_params['Accept'] = 'application/json'  # noqa: E501
        # HTTP header `Content-Type`
        header_params['Content-Type'] = 'application/json'  # noqa: E501
        # JSON indication READY
        dict_body = {}
        dict_body['indication'] = 'READY'
        result = service_api.call_api(url, 'POST', header_params=header_params, path_params = path_params, body=dict_body, async_req=False)
        return 0
    except ApiException as e:
        logger.error('Exception when calling call_api: %s\n' % e)
    return -1
    # End of function send_ready_confirmation

In addition, our MEC application is registering to AppTerminationNotificationSubscription and it needs to delete its subscription when terminating.

At this stage, it is important to note that all subscription deletion use the same format: <subscription URL>/<subscription identifier> (see ETSI MEC GS 003 [16]). 
In this case, it the AppTerminationNotificationSubscription is 'sub-1234', the URIs to do the susbscription and to delete it are:
- MEC_SANDBOX_URL + '/' + sandbox_name + '/' + MEC_PLTF + '/mec_app_support/v2/applications/' + app_inst_id + '/subscriptions'
- MEC_SANDBOX_URL + '/' + sandbox_name + '/' + MEC_PLTF + '/mec_app_support/v2/applications/' + app_inst_id + '/subscriptions/sub-1234'

So, it will be usefull to create a small function to extract the subscription identifier from either the HTTP Location header or from the Link field found into the reponse body data structure. 

#### Subscribing to application termination

In [16]:
def send_subscribe_termination(sandbox_name: str, app_inst_id: swagger_client.models.application_info.ApplicationInfo) -> int:
    global MEC_PLTF, logger

    logger.debug('>>> send_subscribe_termination: ' + app_inst_id.id)
    try:
        url = '/{sandbox_name}/{mec_pltf}/mec_app_support/v2/applications/{app_inst_id}/subscriptions'
        logger.debug('send_subscribe_termination: url: ' + url)
        path_params = {}
        path_params['sandbox_name'] = sandbox_name
        path_params['mec_pltf'] = MEC_PLTF
        path_params['app_inst_id'] = app_inst_id.id
        header_params = {}
        # HTTP header `Accept`
        header_params['Accept'] = 'application/json'  # noqa: E501
        # HTTP header `Content-Type`
        header_params['Content-Type'] = 'application/json'  # noqa: E501
        # Body
        dict_body = {}
        dict_body['subscriptionType'] = 'AppTerminationNotificationSubscription'
        dict_body['callbackReference'] = 'http://yanngarcia.ddns.net/mec011/v2/termination' # FIXME To be parameterized
        dict_body['appInstanceId'] = app_inst_id.id
        (result, status, headers) = service_api.call_api(url, 'POST', header_params=header_params, path_params = path_params, body=dict_body, async_req=False)
        return (extract_sub_id(headers['Location']), headers['Location'])
    except ApiException as e:
        logger.error('Exception when calling call_api: %s\n' % e)
    return None
    # End of function send_subscribe_termination

#### Extracting subscription identifier

In [17]:
def extract_sub_id(resource_url: str) -> str:
    global logger

    logger.debug('>>> extract_sub_id: resource_url: ' + resource_url)

    res = urllib3.util.parse_url(resource_url)
    if res is not None and res.path is not None and res.path != '':
        id = res.path.rsplit('/', 1)[-1]
        if id is not None:
            return id

    return None
    # End of function extract_sub_id

#### Delete subscription to application termination

In [18]:
def delete_subscribe_termination(sandbox_name: str, app_inst_id: swagger_client.models.application_info.ApplicationInfo, sub_id: str) -> int:
    global MEC_PLTF, logger

    logger.debug('>>> delete_subscribe_termination: ' + app_inst_id.id)
    try:
        url = '/{sandbox_name}/{mec_pltf}/mec_app_support/v2/applications/{app_inst_id}/subscriptions/{sub_id}'
        logger.debug('delete_subscribe_termination: url: ' + url)
        path_params = {}
        path_params['sandbox_name'] = sandbox_name
        path_params['mec_pltf'] = MEC_PLTF
        path_params['app_inst_id'] = app_inst_id.id
        path_params['sub_id'] = sub_id
        header_params = {}
        # HTTP header `Accept`
        header_params['Accept'] = 'application/json'  # noqa: E501
        # HTTP header `Content-Type`
        header_params['Content-Type'] = 'application/json'  # noqa: E501
        service_api.call_api(url, 'DELETE', header_params=header_params, path_params = path_params, async_req=False)
        return 0
    except ApiException as e:
        logger.error('Exception when calling call_api: %s\n' % e)
    return -1
    # End of function delete_subscribe_termination

Now, it is time now to create the our fifth iteration of our MEC application.

The sequence is the following:
- Login
- Print sandbox identifier
- Print available network scenarios
- Activate a network scenario
- Request for a new application instance identifier
- Send READY confirmation
- Subscribe to AppTerminationNotificationSubscription
- Check list of services
- Delete AppTerminationNotification subscription
- Delete our application instance identifier
- Deactivate a network scenario
- Logout
- Check that logout is effective


In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Request for a new application instance identifier
        - Send READY confirmation
        
        - Subscribe to AppTermination Notification
        - Send Termination
        - Delete AppTerminationNotification subscription
        - Delete our application instance identifier
        - Deactivate a network scenario
        - Logout
        - Check that logout is effective
    """ 
    global logger, nw_scenarios

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error('Failed to instanciate a MEC Sandbox')
        return

    # Print sandbox identifier
    logger.info('Sandbox created: ' + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error('Failed to retrieve the list of network scenarios')
    elif len(nw_scenarios) != 0:
        logger.info('nw_scenarios: %s', str(type(nw_scenarios[0])))
        logger.info('nw_scenarios: %s', str(nw_scenarios))
        # Wait for the MEC Sandbox is running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running
    else:
        logger.info('nw_scenarios: No scenario available')

    # Activate a network scenario based on a list of criterias (hard coded!!!)
    if activate_network_scenario(sandbox) == -1:
        logger.error('Failed to activate network scenario')
    else:
        logger.info('Network scenario activated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are running
        time.sleep(2 * STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Request for a new application instance identifier
    app_inst_id = request_application_instance_id(sandbox)
    if app_inst_id == None:
        logger.error('Failed to request an application instance identifier')
    else:
        logger.info('app_inst_id: %s', str(app_inst_id))
        time.sleep(STABLE_TIME_OUT)

    # Send READY confirmation
    sub_id = None
    if send_ready_confirmation(sandbox, app_inst_id) == -1:
        logger.error('Failed to send confirm_ready')
    else:
        # Subscribe to AppTerminationNotificationSubscription
        sub_id, res_url = send_subscribe_termination(sandbox, app_inst_id)
        if sub_id == None:
            logger.error('Failed to do the subscription')
        else:
            logger.info('sub_id: %s', sub_id)

    # Any processing here
    time.sleep(STABLE_TIME_OUT)

    # Delete AppTerminationNotification subscription
    if sub_id is not None:
        if delete_subscribe_termination(sandbox, app_inst_id, sub_id) == -1:
            logger.error('Failed to delete the application instance identifier')
        else:
            logger.info('app_inst_id deleted: ' + app_inst_id.id)

    # Delete the application instance identifier
    if delete_application_instance_id(sandbox, app_inst_id.id) == -1:
        logger.error('Failed to delete the application instance identifier')
    else:
        logger.info('app_inst_id deleted: ' + app_inst_id.id)

    # Deactivate a network scenario based on a list of criterias (hard coded!!!)
    if deactivate_network_scenario(sandbox) == -1:
        logger.error('Failed to deactivate network scenario')
    else:
        logger.info('Network scenario deactivated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are terminated
        time.sleep(2 * STABLE_TIME_OUT)

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug('To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A)')
  
    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()

### Conclusion: Create two procedures for the setup and the termination of our MEC application


#### The procedure for the setup of a MEC application

This function provides the steps to setup a MEC application and to be ready to use the MEC service exposed by the created MEC Sandbox.


In [19]:
def mec_app_setup():
    """
    This function provides the steps to setup a MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Request for a new application instance identifier
        - Send READY confirmation
        - Subscribe to AppTermination Notification
    """
    global logger, nw_scenarios

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error('Failed to instanciate a MEC Sandbox')
        return
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error('Failed to retrieve the list of network scenarios')
    elif len(nw_scenarios) != 0:
        # Wait for the MEC Sandbox is running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running
    else:
        logger.info('nw_scenarios: No scenario available')

    # Activate a network scenario based on a list of criterias (hard coded!!!)
    if activate_network_scenario(sandbox) == -1:
        logger.error('Failed to activate network scenario')
    else:
        # Wait for the MEC services are running
        time.sleep(2 * STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Request for a new application instance identifier
    app_inst_id = request_application_instance_id(sandbox)
    if app_inst_id == None:
        logger.error('Failed to request an application instance identifier')
    else:
        # Wait for the MEC services are terminated
        time.sleep(STABLE_TIME_OUT)

    # Send READY confirmation
    sub_id = None
    if send_ready_confirmation(sandbox, app_inst_id) == -1:
        logger.error('Failed to send confirm_ready')
    else:
        # Subscribe to AppTerminationNotificationSubscription
        sub_id, res_url = send_subscribe_termination(sandbox, app_inst_id)
        if sub_id == None:
            logger.error('Failed to do the subscription')

    return (sandbox, app_inst_id, sub_id)
    # End of function mec_app_setup

#### The procedure for the termination of a MEC application

This function provides the steps to terminate a MEC application.

NOTE: All subscriptions done outside of the mec_app_setup function are not deleted.

In [20]:
def mec_app_termination(sandbox: str, app_inst_id:swagger_client.models.ApplicationInfo, sub_id: str):
    """
    This function provides the steps to setup a MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Request for a new application instance identifier
        - Send READY confirmation
        - Subscribe to AppTermination Notification
    """
    # Delete AppTerminationNotification subscription
    if sub_id is not None:
        if delete_subscribe_termination(sandbox, app_inst_id, sub_id) == -1:
            logger.error('Failed to delete the application instance identifier')

    # Delete the application instance identifier
    if delete_application_instance_id(sandbox, app_inst_id.id) == -1:
        logger.error('Failed to delete the application instance identifier')
    else:
        # Wait for the MEC services are terminated
        time.sleep(STABLE_TIME_OUT)

    # Deactivate a network scenario based on a list of criterias (hard coded!!!)
    if deactivate_network_scenario(sandbox) == -1:
        logger.error('Failed to deactivate network scenario')
    else:
        # Wait for the MEC services are terminated
        time.sleep(2 * STABLE_TIME_OUT)

    # Logout
    process_logout(sandbox)

    # End of function mec_app_termination

The following cell descrbes the new basic MEC application architecture. It will be used in the rest of this titorial.

In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Mec application setup
        - Get UU unicast provisioning information
        - Mec application termination
    """ 
    global logger, nw_scenarios

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Setup the MEC application
    (sandbox_name, app_inst_id, sub_id) = mec_app_setup()

    # Any processing here
    logger.info('sandbox_name: ' + sandbox_name)
    logger.info('app_inst_id: ' + app_inst_id.id)
    if sub_id is not None:
        logger.info('sub_id: ' + sub_id)
    time.sleep(STABLE_TIME_OUT)

    # Terminate the MEC application
    mec_app_termination(sandbox_name, app_inst_id, sub_id)

    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()

## Create our second MEC application: how to use MEC Services

After doing the logging, network scenario activation, MEC application instance creation steps, we are ready to exploit the MEC services exposed by the MEC Sandbox.

In this clause, we use the following functionalities provided by MEC-030:
- Getting UU unicast provisioning information (ETSI GS MEC 030 Clause 5.5.1)
- Subscribe to the V2X message distribution server (ETSI GS MEC 030 Clause 5.5.7)
- Delete subscription


### Getting UU unicast provisioning information

The purpose is to query provisioning information for V2X communication over Uu unicast.

In [21]:
def send_uu_unicast_provisioning_info(sandbox_name: str, ecgi: str) -> str:
    global MEC_PLTF, logger

    logger.debug('>>> send_uu_unicast_provisioning_info: ' + ecgi)
    try:
        url = '/{sandbox_name}/{mec_pltf}/vis/v2/queries/uu_unicast_provisioning_info'
        logger.debug('send_uu_unicast_provisioning_info: url: ' + url)
        path_params = {}
        path_params['sandbox_name'] = sandbox_name
        path_params['mec_pltf'] = MEC_PLTF
        query_params = []
        query_params.append(('location_info', 'ecgi,' + ecgi))
        header_params = {}
        # HTTP header `Accept`
        header_params['Accept'] = 'application/json'  # noqa: E501
        # HTTP header `Content-Type`
        header_params['Content-Type'] = 'application/json'  # noqa: E501
        result = service_api.call_api(url, 'GET', header_params=header_params, path_params=path_params, query_params=query_params, async_req=False)
        return result
    except ApiException as e:
        logger.error('Exception when calling call_api: %s\n' % e)
    return None
    # End of function send_uu_unicast_provisioning_info

Let's create the our second MEC application.
The sequence is the following:
- Mec application setup
- Get UU unicast provisioning information
- Mec application termination

Note that the UU unicast provisioning information is returned as a JSON string. To de-serialized it into a Python data structure, please refer to clause [Subscribing to V2X message distribution server](#subscribing_to_v2x_message_distribution_server).

In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Mec application setup
        - Get UU unicast provisioning information
        - Mec application termination
    """ 
    global logger, nw_scenarios

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Setup the MEC application
    (sandbox_name, app_inst_id, sub_id) = mec_app_setup()

    # Get UU unicast provisioning information
    ecgi = "268708941961,268711972264" # List of ecgi spearated by a ','
    result = send_uu_unicast_provisioning_info(sandbox_name, ecgi)
    if result is None:
        logger.error('Failed to get UU unicast provisioning information')
    else:
        logger.info('UU unicast provisioning information: ', str(result))

    # Terminate the MEC application
    mec_app_termination(sandbox_name, app_inst_id, sub_id)

    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()

### Subscribing to V2X message distribution server

Here, we need to come back to the MEC 030 standard to create the type V2xMsgSubscription. It involves the creation of a set of basic types described below.

Note: These new type shall be 'JSON"serializable. It means that they have to implement the following methods:
```python
to_dict()
to_str()
__repr__()
__eq__()
__ne__()
```
`
}



In [54]:
class LinkType(object):
    swagger_types = {'href': 'str'}
    attribute_map = {'href': 'href'}
    def __init__(self, href=None):  # noqa: E501
        self._href = None
        if href is not None:
            self._href = href
    @property
    def href(self):
        return self._href
    @href.setter
    def href(self, href):
        self._href = href
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(
                    lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,
                    value
                ))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(LinkType, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, LinkType):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class Links(object):
    swagger_types = {'self': 'LinkType'}
    attribute_map = {'self': 'self'}
    def __init__(self, self_=None):  # noqa: E501
        self._self = None
        if self_ is not None:
            self._self = self_
    @property
    def self_(self):
        return self._self
    @self_.setter
    def self_(self, self_):
        self._self = self_
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(
                    lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,
                    value
                ))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(Links, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, Links):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class TimeStamp(object):
    swagger_types = {'seconds': 'int', 'nano_seconds': 'int'}
    attribute_map = {'seconds': 'seconds', 'nano_seconds': 'nanoSeconds'}
    def __init__(self, seconds=None, nano_seconds=None):  # noqa: E501
        self._seconds = None
        self._nano_seconds = None
        if seconds is not None:
            self._seconds = seconds
        if nano_seconds is not None:
            self._nano_seconds = nano_seconds
    @property
    def seconds(self):
        return self._seconds
    @seconds.setter
    def seconds(self, seconds):
        self._seconds = seconds
    @property
    def nano_seconds(self):
        return self._nano_seconds
    @nano_seconds.setter
    def nano_seconds(self, nano_seconds):
        self._nano_seconds = nano_seconds
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(
                    lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,
                    value
                ))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(TimeStamp, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, TimeStamp):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

### Subscribing to V2X message distribution server

The cell bellow implements the V2xMsgSubscription data structure."`
}



In [23]:
class V2xMsgSubscription(object):
    swagger_types = {'links': 'Links', 'callback_reference': 'str', 'filter_criteria': 'V2xMsgSubscriptionFilterCriteria', 'request_test_notification': 'bool', 'subscription_type': 'str'}
    attribute_map = {'links': 'Links', 'callback_reference': 'callbackReference', 'filter_criteria': 'filterCriteria', 'request_test_notification': 'requestTestNotification', 'subscription_type': 'subscriptionType'}
    def __init__(self, links=None, callback_reference=None, filter_criteria=None, request_test_notification=None):  # noqa: E501
        self._links = None
        self._callback_reference = None
        self._filter_criteria = None
        self._request_test_notification = None
        self._subscription_type = "V2xMsgSubscription"
        if links is not None:
            self.links = links
        if callback_reference is not None:
            self.callback_reference = callback_reference
        if filter_criteria is not None:
            self.filter_criteria = filter_criteria
        if request_test_notification is not None:
            self.request_test_notification = request_test_notification
    @property
    def links(self):
        return self._links
    @links.setter
    def links(self, links):
        self_.links = links
    @property
    def callback_reference(self):
        return self._callback_reference
    @callback_reference.setter
    def callback_reference(self, callback_reference):
        self._callback_reference = callback_reference
    @property
    def links(self):
        return self._links
    @links.setter
    def links(self, links):
        self._links = links
    @property
    def filter_criteria(self):
        return self._filter_criteria
    @filter_criteria.setter
    def filter_criteria(self, filter_criteria):
        self._filter_criteria = filter_criteria
    @property
    def request_test_notification(self):
        return self._request_test_notification
    @request_test_notification.setter
    def request_test_notification(self, request_test_notification):
        self._request_test_notification = request_test_notification
    @property
    def subscription_type(self):
        return self._subscription_type
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(
                    lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,
                    value
                ))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(V2xMsgSubscription, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, V2xMsgSubscription):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class V2xMsgSubscriptionFilterCriteria(object):
    swagger_types = {'msg_type': 'list[str]', 'std_organization': 'str'}
    attribute_map = {'msg_type': 'MsgType', 'std_organization': 'stdOrganization'}
    def __init__(self, msg_type, std_organization):  # noqa: E501
        self._msg_type = None
        self._std_organization = None
        self.msg_type = msg_type
        self.std_organization = std_organization
    @property
    def msg_type(self):
        return self._msg_type
    @msg_type.setter
    def msg_type(self, msg_type):
        self._msg_type = msg_type
    @property
    def std_organization(self):
        return self._std_organization
    @std_organization.setter
    def std_organization(self, std_organization):
        self._std_organization = std_organization
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(
                    lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,
                    value
                ))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(V2xMsgSubscriptionFilterCriteria, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, V2xMsgSubscriptionFilterCriteria):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

Here is the V2X message subscription function. The body contains a 'JSON' serialized instance of the class V2xMsgSubscription.

In [34]:
def subscribe_v2x_message(sandbox_name: str, v2xMsgSubscription: V2xMsgSubscription) -> int:
    global MEC_SANDBOX_URL, MEC_PLTF, CALLBACK_URI, logger

    logger.debug('>>> subscribe_v2x_message: v2xMsgSubscription: ' + str(v2xMsgSubscription))
    try:
        url = '/{sandbox_name}/{mec_pltf}/vis/v2/subscriptions'
        logger.debug('subscribe_v2x_message: url: ' + url)
        path_params = {}
        path_params['sandbox_name'] = sandbox_name
        path_params['mec_pltf'] = MEC_PLTF
        header_params = {}
        # HTTP header `Accept`
        header_params['Accept'] = 'application/json'  # noqa: E501
        # HTTP header `Content-Type`
        header_params['Content-Type'] = 'application/json'  # noqa: E501
        (result, status, headers) = service_api.call_api(url, 'POST', header_params=header_params, path_params=path_params, body=v2xMsgSubscription, async_req=False)
        return (extract_sub_id(headers['Location']), headers['Location'])
    except ApiException as e:
        logger.error('Exception when calling call_api: %s\n' % e)
    return None
    # End of function subscribe_v2x_message

Here is a generic function to delete any MEC service subscription based on the subscription resource URL provided in the Location header of the subscription creation response.

In [40]:
def delete_mec_subscription(resource_url: str) -> int:
    global logger

    logger.debug('>>> delete_mec_subscription: resource_url: ' + resource_url)
    try:
        res = urllib3.util.parse_url(resource_url)
        if res is None:
            logger.error('delete_mec_subscription: Failed to paerse URL')
            return -1
        header_params = {}
        # HTTP header `Accept`
        header_params['Accept'] = 'application/json'  # noqa: E501
        # HTTP header `Content-Type`
        header_params['Content-Type'] = 'application/json'  # noqa: E501
        service_api.call_api(res.path, 'DELETE', header_params=header_params, async_req=False)
        return 0
    except ApiException as e:
        logger.error('Exception when calling call_api: %s\n' % e)
    return -1


Finaly, here is how to implement the V2X message subscription:

In [41]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Mec application setup
        - Subscribe to V2XMessage
        - Delete subscription
        - Mec application termination
    """ 
    global MEC_PLTF, CALLBACK_URI, logger

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Setup the MEC application
    (sandbox_name, app_inst_id, sub_id) = mec_app_setup()

    # Create a V2X message subscritpion
    filter_criteria = V2xMsgSubscriptionFilterCriteria(['1', '2'], 'ETSI')
    v2xMsgSubscription = V2xMsgSubscription(callback_reference = CALLBACK_URI + '/vis/v2/v2x_msg_notification', filter_criteria = filter_criteria)
    v2x_sub_id, v2x_resource = subscribe_v2x_message(sandbox_name, v2xMsgSubscription)
    if v2x_sub_id is None:
        logger.error('Failed to get UU unicast provisioning information')

    # Any processing here
    logger.info('sandbox_name: ' + sandbox_name)
    logger.info('app_inst_id: ' + app_inst_id.id)
    if sub_id is not None:
        logger.info('sub_id: ' + sub_id)
    time.sleep(STABLE_TIME_OUT)

    # Delete the V2X message subscritpion
    delete_mec_subscription(v2x_resource)

    # Terminate the MEC application
    mec_app_termination(sandbox_name, app_inst_id, sub_id)

    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()

2024-10-01 12:51:59,320 - __main__ - DEBUG - Starting at 20241001-125159
2024-10-01 12:51:59,321 - __main__ - DEBUG - 	 pwd= /home/yann/dev/jupyter/Sandbox/mecapp
2024-10-01 12:51:59,322 - __main__ - DEBUG - >>> process_login
2024-10-01 12:51:59,322 DEBUG Resetting dropped connection: mec-platform2.etsi.org
2024-10-01 12:51:59,505 DEBUG https://mec-platform2.etsi.org:443 "POST /sandbox-api/v1/login?provider=Jupyter2024 HTTP/1.1" 201 48
2024-10-01 12:51:59,506 DEBUG response body: b'{"user_code":"sbx5bl4at0","verification_uri":""}'
2024-10-01 12:51:59,507 - __main__ - DEBUG - process_login (step1): oauth: {'user_code': 'sbx5bl4at0', 'verification_uri': ''}
2024-10-01 12:51:59,507 - __main__ - DEBUG - =======================> DO AUTHORIZATION WITH CODE : sbx5bl4at0
2024-10-01 12:51:59,508 - __main__ - DEBUG - =======================> DO AUTHORIZATION HERE :      


send: b'POST /sandbox-api/v1/login?provider=Jupyter2024 HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nAccept: application/json\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{}'
reply: 'HTTP/1.1 201 Created\r\n'
header: Date: Tue, 01 Oct 2024 10:51:58 GMT
header: Content-Type: application/json; charset=UTF-8
header: Content-Length: 48
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


2024-10-01 12:52:02,541 DEBUG https://mec-platform2.etsi.org:443 "GET /sandbox-api/v1/namespace?user_code=sbx5bl4at0 HTTP/1.1" 200 29
2024-10-01 12:52:02,543 DEBUG response body: b'{"sandbox_name":"sbx5bl4at0"}'
2024-10-01 12:52:02,546 - __main__ - DEBUG - process_login (step2): result: {'sandbox_name': 'sbx5bl4at0'}


send: b'GET /sandbox-api/v1/namespace?user_code=sbx5bl4at0 HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nAccept: application/json\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Date: Tue, 01 Oct 2024 10:52:01 GMT
header: Content-Type: application/json; charset=UTF-8
header: Content-Length: 29
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


2024-10-01 12:52:08,554 - __main__ - DEBUG - >>> get_network_scenarios: sandbox=sbx5bl4at0
2024-10-01 12:52:08,558 DEBUG Resetting dropped connection: mec-platform2.etsi.org
2024-10-01 12:52:08,744 DEBUG https://mec-platform2.etsi.org:443 "GET /sandbox-api/v1/sandboxNetworkScenarios?sandbox_name=sbx5bl4at0 HTTP/1.1" 200 157
2024-10-01 12:52:08,747 DEBUG response body: b'[{"id":"4g-5g-macro-v2x"},{"id":"4g-5g-wifi-macro"},{"id":"4g-macro"},{"id":"4g-wifi-macro"},{"id":"dual-mep-4g-5g-wifi-macro"},{"id":"dual-mep-short-path"}]'
2024-10-01 12:52:08,750 - __main__ - DEBUG - get_network_scenarios: result: [{'id': '4g-5g-macro-v2x'}, {'id': '4g-5g-wifi-macro'}, {'id': '4g-macro'}, {'id': '4g-wifi-macro'}, {'id': 'dual-mep-4g-5g-wifi-macro'}, {'id': 'dual-mep-short-path'}]


...

reply: 'HTTP/1.1 204 No Content\r\n'
header: Date: Tue, 01 Oct 2024 10:52:40 GMT
header: Content-Type: application/json; charset=UTF-8
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains
send: b'DELETE /sbx5bl4at0/mep1/mec_app_support/v2/applications/ae79ecfc-b6c8-457a-b67b-40bf019ac568/subscriptions/sub-YamGx8Gewxznv4X7 HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nAccept: application/json\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{}'
reply: 'HTTP/1.1 204 No Content\r\n'
header: Date: Tue, 01 Oct 2024 10:52:40 GMT
header: Content-Type: application/json; charset=UTF-8
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains
send: b'DELETE /sandbox-api/v1/sandboxAppInstances/sbx5bl4at0/ae79ecfc-b6c8-457a-b67b-40bf019ac568 HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\n

2024-10-01 12:52:47,452 - __main__ - DEBUG - >>> deactivate_network_scenario: sbx5bl4at0
2024-10-01 12:52:47,507 DEBUG https://mec-platform2.etsi.org:443 "DELETE /sandbox-api/v1/sandboxNetworkScenarios/sbx5bl4at0/4g-5g-macro-v2x HTTP/1.1" 204 0
2024-10-01 12:52:47,510 DEBUG response body: b''


send: b'DELETE /sandbox-api/v1/sandboxNetworkScenarios/sbx5bl4at0/4g-5g-macro-v2x HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{}'
reply: 'HTTP/1.1 204 No Content\r\n'
header: Date: Tue, 01 Oct 2024 10:52:46 GMT
header: Content-Type: application/json; charset=UTF-8
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


2024-10-01 12:52:59,523 - __main__ - DEBUG - >>> process_logout: sandbox=sbx5bl4at0
2024-10-01 12:52:59,526 DEBUG Resetting dropped connection: mec-platform2.etsi.org
2024-10-01 12:52:59,697 DEBUG https://mec-platform2.etsi.org:443 "POST /sandbox-api/v1/logout?sandbox_name=sbx5bl4at0 HTTP/1.1" 204 0
2024-10-01 12:52:59,699 DEBUG response body: b''
2024-10-01 12:52:59,700 - __main__ - DEBUG - Stopped at 20241001-125259


send: b'POST /sandbox-api/v1/logout?sandbox_name=sbx5bl4at0 HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{}'
reply: 'HTTP/1.1 204 No Content\r\n'
header: Date: Tue, 01 Oct 2024 10:52:59 GMT
header: Content-Type: application/json; charset=UTF-8
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


### Notification support

To recieve notifcation, our MEC application is required to support an HTTP listenener to recieve POST request from the MEC Sandbox and replto repry to them: this is the notification mechanism.

The class HTTPRequestHandler (see cell below) provides the suport of such mechanism.


In [42]:
class HTTPRequestHandler(BaseHTTPRequestHandler):
    global logger

    def do_POST(self):
        if re.search(CALLBACK_URI, self.path):
            ctype, pdict = _parse_header(self.headers.get('content-type'))
            if ctype == "application/json":
                length = int(self.headers.get('content-length'))
                rfile_str = self.rfile.read(length).decode('utf8')
                data = parse.parse_qs(rfile_str, keep_blank_values=True)
                record_id = self.path.split('/')[-1]
                LocalData.records[record_id] = data
                logger.info('addrecord %s: %s' % (record_id, data))
                self.send_response(HTTPStatus.OK)
            else:
                self.send_response(HTTPStatus.BAD_REQUEST, 'Only application/json is supported')
        else:
            self.send_response(HTTPStatus.BAD_REQUEST, 'Unsupported URI')
        self.end_headers()

    def do_GET(self):
        self.send_response(HTTPStatus.BAD_REQUEST)
        self.end_headers()
    # End of class HTTPRequestHandler

class LocalData(object):
    records = {}
    # End of class LocalData

### Put all together

let's add a subscription the our previous MEC application.
The sequence is the following:
- Mec application setup
- Get UU unicast provisioning information
- Add subscription
- Mec application termination

In [44]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Mec application setup
        - Get UU unicast provisioning information
        - Add subscription
        - Mec application termination
    """ 
    global logger

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Setup the MEC application
    (sandbox_name, app_inst_id, sub_id) = mec_app_setup()

    # Get UU unicast provisioning information
    ecgi = "268708941961,268711972264" # List of ecgi spearated by a ','
    result = send_uu_unicast_provisioning_info(sandbox_name, ecgi)
    if result is None:
        logger.error('Failed to get UU unicast provisioning information')
    else:
        logger.info('UU unicast provisioning information: ', str(result))

    # Start notification server in a daemonized thread
    notification_server = threading.Thread(name='notification_server', target=HTTPRequestHandler, args=(LISTENER_IP, LISTENER_PORT))
    notification_server.setDaemon(True) # Set as a daemon so it will be killed once the main thread is dead.
    notification_server.start()
    # Continue

    # Create a V2X message subscritpion
    filter_criteria = V2xMsgSubscriptionFilterCriteria(['1', '2'], 'ETSI')
    v2xMsgSubscription = V2xMsgSubscription(callback_reference = CALLBACK_URI + '/vis/v2/v2x_msg_notification', filter_criteria = filter_criteria)
    v2x_sub_id, v2x_resource = subscribe_v2x_message(sandbox_name, v2xMsgSubscription)
    if v2x_sub_id is None:
        logger.error('Failed to get UU unicast provisioning information')

    # Any processing here
    logger.info('v2x_sub_id: ' + v2x_sub_id)
    logger.info('v2x_resource: ' + v2x_resource)
    time.sleep(STABLE_TIME_OUT)

    # Delete the V2X message subscritpion
    delete_mec_subscription(v2x_resource)

    # Terminate the MEC application
    mec_app_termination(sandbox_name, app_inst_id, sub_id)

    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


2024-10-01 12:58:31,914 - __main__ - DEBUG - Starting at 20241001-125831
2024-10-01 12:58:31,917 - __main__ - DEBUG - 	 pwd= /home/yann/dev/jupyter/Sandbox/mecapp
2024-10-01 12:58:31,919 - __main__ - DEBUG - >>> process_login
2024-10-01 12:58:31,922 DEBUG Resetting dropped connection: mec-platform2.etsi.org
2024-10-01 12:58:32,109 DEBUG https://mec-platform2.etsi.org:443 "POST /sandbox-api/v1/login?provider=Jupyter2024 HTTP/1.1" 201 48
2024-10-01 12:58:32,111 DEBUG response body: b'{"user_code":"sbxsn3v6jl","verification_uri":""}'
2024-10-01 12:58:32,114 - __main__ - DEBUG - process_login (step1): oauth: {'user_code': 'sbxsn3v6jl', 'verification_uri': ''}
2024-10-01 12:58:32,118 - __main__ - DEBUG - =======================> DO AUTHORIZATION WITH CODE : sbxsn3v6jl
2024-10-01 12:58:32,120 - __main__ - DEBUG - =======================> DO AUTHORIZATION HERE :      


send: b'POST /sandbox-api/v1/login?provider=Jupyter2024 HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nAccept: application/json\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{}'
reply: 'HTTP/1.1 201 Created\r\n'
header: Date: Tue, 01 Oct 2024 10:58:31 GMT
header: Content-Type: application/json; charset=UTF-8
header: Content-Length: 48
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


2024-10-01 12:58:35,155 DEBUG https://mec-platform2.etsi.org:443 "GET /sandbox-api/v1/namespace?user_code=sbxsn3v6jl HTTP/1.1" 200 29
2024-10-01 12:58:35,158 DEBUG response body: b'{"sandbox_name":"sbxsn3v6jl"}'
2024-10-01 12:58:35,160 - __main__ - DEBUG - process_login (step2): result: {'sandbox_name': 'sbxsn3v6jl'}


send: b'GET /sandbox-api/v1/namespace?user_code=sbxsn3v6jl HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nAccept: application/json\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Date: Tue, 01 Oct 2024 10:58:34 GMT
header: Content-Type: application/json; charset=UTF-8
header: Content-Length: 29
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


2024-10-01 12:58:41,167 - __main__ - DEBUG - >>> get_network_scenarios: sandbox=sbxsn3v6jl
2024-10-01 12:58:41,170 DEBUG Resetting dropped connection: mec-platform2.etsi.org
2024-10-01 12:58:41,356 DEBUG https://mec-platform2.etsi.org:443 "GET /sandbox-api/v1/sandboxNetworkScenarios?sandbox_name=sbxsn3v6jl HTTP/1.1" 200 157
2024-10-01 12:58:41,358 DEBUG response body: b'[{"id":"4g-5g-macro-v2x"},{"id":"4g-5g-wifi-macro"},{"id":"4g-macro"},{"id":"4g-wifi-macro"},{"id":"dual-mep-4g-5g-wifi-macro"},{"id":"dual-mep-short-path"}]'
2024-10-01 12:58:41,361 - __main__ - DEBUG - get_network_scenarios: result: [{'id': '4g-5g-macro-v2x'}, {'id': '4g-5g-wifi-macro'}, {'id': '4g-macro'}, {'id': '4g-wifi-macro'}, {'id': 'dual-mep-4g-5g-wifi-macro'}, {'id': 'dual-mep-short-path'}]


...

reply: 'HTTP/1.1 204 No Content\r\n'
header: Date: Tue, 01 Oct 2024 10:59:13 GMT
header: Content-Type: application/json; charset=UTF-8
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains
send: b'DELETE /sbxsn3v6jl/mep1/mec_app_support/v2/applications/b49b3ae3-1fd9-48c6-9282-d449dfbba42e/subscriptions/sub-j1XbzihrdTWo-CRi HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nAccept: application/json\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{}'
reply: 'HTTP/1.1 204 No Content\r\n'
header: Date: Tue, 01 Oct 2024 10:59:13 GMT
header: Content-Type: application/json; charset=UTF-8
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains
send: b'DELETE /sandbox-api/v1/sandboxAppInstances/sbxsn3v6jl/b49b3ae3-1fd9-48c6-9282-d449dfbba42e HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\n

2024-10-01 12:59:20,042 - __main__ - DEBUG - >>> deactivate_network_scenario: sbxsn3v6jl
2024-10-01 12:59:20,103 DEBUG https://mec-platform2.etsi.org:443 "DELETE /sandbox-api/v1/sandboxNetworkScenarios/sbxsn3v6jl/4g-5g-macro-v2x HTTP/1.1" 204 0
2024-10-01 12:59:20,105 DEBUG response body: b''


send: b'DELETE /sandbox-api/v1/sandboxNetworkScenarios/sbxsn3v6jl/4g-5g-macro-v2x HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{}'
reply: 'HTTP/1.1 204 No Content\r\n'
header: Date: Tue, 01 Oct 2024 10:59:19 GMT
header: Content-Type: application/json; charset=UTF-8
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


2024-10-01 12:59:32,119 - __main__ - DEBUG - >>> process_logout: sandbox=sbxsn3v6jl
2024-10-01 12:59:32,122 DEBUG Resetting dropped connection: mec-platform2.etsi.org
2024-10-01 12:59:32,298 DEBUG https://mec-platform2.etsi.org:443 "POST /sandbox-api/v1/logout?sandbox_name=sbxsn3v6jl HTTP/1.1" 204 0
2024-10-01 12:59:32,300 DEBUG response body: b''
2024-10-01 12:59:32,301 - __main__ - DEBUG - Stopped at 20241001-125932


send: b'POST /sandbox-api/v1/logout?sandbox_name=sbxsn3v6jl HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{}'
reply: 'HTTP/1.1 204 No Content\r\n'
header: Date: Tue, 01 Oct 2024 10:59:31 GMT
header: Content-Type: application/json; charset=UTF-8
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


## Create our third MEC application: how to use V2X QoS Prediction

The MEC Sanbox V2X QoS Prediction is based on a grid Map of Monaco City where areas are categorized into residential, commercial and coastal. 
PoA (Point Of Access) s are categorized depending on where they lie in each grid 
Each category has its own traffic load patterns which are pre-determin. The V2X QoS PredictionPF) will give more accurate values of RSRP and RSRQ based on the diurnal traffic patterns for each z.
The network scenario named "4g-5g-v2x-macro" must be used to get access to the V2X QoS Prediction feature.)
b>Not - > The MEC Sanbox V2X QoS Predicti PF is enabled when the PredictedQos.routes.routeInfo.time attribute is present in threquest qu(ETSI GS MEC 030 Clause 6.2.6 Type: Predicd QoSeQo
- Limitations:
1. The Location Granularity is currently not being validated as RSRP/RSRP calculations are done at the exact location provided by the user.2 
Time Granularity is currently not supported by the Prediction Function (design limitations of the minimal, emulated, pre-determined traffic prediction mel.).3.  
Upper limit on the number of elements (10 each) in the routes and routeInfo structures (arrays) to not affect user experience and response encyoy



The table below describes the excepted Qos with and without the prediction model in deiffretnarea and at different time.


|     Location        |               Time                  |      PoA         |  Category   |    Status     | QoS without Prediction Model | QoS with Prediction Model | Expected |
| 	              | (Unix time in sec) | Standard (GMT) |                  |             |               |    RSRP        |   RSRQ      |    RSRP     |   RSRQ      |          |
| ------------------- | -----------        | -------------- | ---------------- | ----------- | ------------- | -------------- | ----------- | ----------- | ----------- | -------- |
| 43.729416,7.414853  |     1653295620     |    08:47:00    | 4g-macro-cell-2  | Residential | Congested     |     63         |     21      |     60      |     20      |   Yes    |
| 43.732456,7.418417  |     1653299220     |    09:47:00    | 4g-macro-cell-3  | Residential | Not Congested |     55         |     13      |     55      |     13      |   Yes    |
| 43.73692,7.4209256  |     1653302820     |    10:47:00    | 4g-macro-cell-6  | Coastal     | Not Congested |     68         |     26      |     68      |     26      |   Yes    |
| 43.738007,7.4230533 |     1653305220     |    11:27:00    | 4g-macro-cell-6  | Coastal     | Not Congested |     55         |     13      |     55      |     13      |   Yes    |
| 43.739685,7.424881  |     1653308820     |    12:27:00    | 4g-macro-cell-7  | Commercial  | Congested     |     63         |     21      |     40      |     13      |   Yes    |
| 43.74103,7.425759   |     1653312600     |    13:30:00    | 4g-macro-cell-7  | Commercial  | Congested     |     56         |     14      |     40      |     8       |   Yes    |
| 43.74258,7.4277945  |     1653315900     |    14:25:00    | 4g-macro-cell-8  | Coastal     | Congested     |     59         |     17      |     47      |     13      |   Yes    |
| 43.744972,7.4295254 |     1653318900     |    15:15:00    | 4g-macro-cell-8  | Coastal     | Congested     |     53         |     11      |     40      |     5       |   Yes    |
| 43.74773,7.4320855  |     1653322500     |    16:15:00    | 5g-small-cell-14 | Commercial  | Congested     |     78         |     69      |     60      |     53      |   Yes    |
| 43.749264,7.435894  |     1653329700     |    18:15:00    | 5g-small-cell-20 | Commercial  | Not Congested |     84         |     72      |     84      |     72      |  Yes    |	72	84	72	Yes



Here is an example of a basic V2X predicted QoS request based on two point in path at 8am in Residential area:
```json
{
  "predictionTarget": "SINGLE_UE_PREDICTION",
  "timeGranularity": null,
  "locationGranularity": "30",
  "routes": [
      {
        "routeInfo": [
          {
            "location": {
              "geoArea": {
                "latitude": 43.729416,
                "longitude": 7.414853
              }
            },
            "time": {
              "nanoSeconds": 0,
              "seconds": 1653295620
            }
          },
          {
              "location": {
                "geoArea": {
                  "latitude": 43.732456,
                  "longitude": 7.418417
                }
              },
            "time": {
              "nanoSeconds": 0,
              "seconds": 1653299220
            }
         
   }
Let first create the required types before to prepare a V2X Predicted QoS request based on the JSON above.
        ]
      }
    ]
}```


In [84]:
class Routes(object):
    swagger_types = {'_route_info': 'list[RouteInfo]'}
    attribute_map = {'_route_info': 'routeInfo'}
    def __init__(self, route_info:list):  # noqa: E501
        self._route_info = None
        self.route_info = route_info
    @property
    def route_info(self):
        return self._route_info
    @route_info.setter
    def route_info(self, route_info):
        self._route_info = route_info
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,value))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(Routes, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, Routes):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class LocationInfo(object):
    swagger_types = {'_ecgi': 'Ecgi', '_geo_area': 'LocationInfoGeoArea'}
    attribute_map = {'_ecgi': 'ecgi', '_geo_area': 'geoArea'}
    def __init__(self, ecgi=None, geo_area=None):  # noqa: E501
        self._ecgi = None
        self._geo_area = None
        if ecgi is not None:
            self.ecgi = ecgi
        if geo_area is not None:
            self.geo_area = geo_area
    @property
    def ecgi(self):
        return self._ecgi
    @ecgi.setter
    def ecgi(self, ecgi):
        self._ecgi = ecgi
    @property
    def geo_area(self):
        return self._geo_area
    @geo_area.setter
    def geo_area(self, geo_area):
        self._geo_area = geo_area
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,value))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(LocationInfo, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, LocationInfo):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class RouteInfo(object):
    swagger_types = {'_location': 'LocationInfo', '_time_stamp': 'TimeStamp'}
    attribute_map = {'_location': 'location', '_time_stamp': 'time'}
    def __init__(self, location:LocationInfo, time_stamp=None):  # noqa: E501
        self._location = None
        self.location = location
        self._time_stamp = None
        if time_stamp is not None:
            self.time_stamp = time_stamp
    @property
    def location(self):
        return self._location
    @location.setter
    def location(self, location):
        self._location = location
    @property
    def time_stamp(self):
        return self._time_stamp
    @time_stamp.setter
    def time_stamp(self, time_stamp):
        self._time_stamp = time_stamp
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,value))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(RouteInfo, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, RouteInfo):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class LocationInfoGeoArea(object):
    swagger_types = {'_latitude': 'float', '_longitude': 'float'}
    attribute_map = {'_latitude': 'latitude', '_longitude': 'longitude'}
    def __init__(self, ecgi=None, geo_area=None):  # noqa: E501
        self._latitude = None
        self._longitude = None
        if latitude is not None:
            self.latitude = latitude
        if longitude is not None:
            self.longitude = longitude
    @property
    def latitude(self):
        return self._latitude
    @latitude.setter
    def latitude(self, latitude):
        self._latitude = latitude
    @property
    def longitude(self):
        return self._longitude
    @longitude.setter
    def longitude(self, longitude):
        self._longitude = longitude
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,value))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(LocationInfoGeoArea, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, LocationInfoGeoArea):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class Ecgi(object):
    swagger_types = {'_cellId': 'CellId', '_plmn': 'Plmn'}
    attribute_map = {'_cellId': 'cellId', '_plmn': 'plmn'}
    def __init__(self, cellId=None, plmn=None):  # noqa: E501
        self._cellId = None
        self._plmn = None
        if cellId is not None:
            self.cellId = cellId
        if plmn is not None:
            self.plmn = plmn
    @property
    def cellId(self):
        return self._cellId
    @cellId.setter
    def cellId(self, cellId):
        self._cellId = cellId
    @property
    def plmn(self):
        return self._plmn
    @plmn.setter
    def plmn(self, plmn):
        self._plmn = plmn
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,value))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(Ecgi, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, Ecgi):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class CellId(object):
    swagger_types = {'_cellId': 'str'}
    attribute_map = {'_cellId': 'cellId'}
    def __init__(self, cellId):  # noqa: E501
        self._cellId = None
        self.cellId = cellId
    @property
    def cellId(self):
        return self._cellId
    @cellId.setter
    def cellId(self, cellId):
        self._cellId = cellId
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,value))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(CellId, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, CellId):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class Plmn(object):
    swagger_types = {'_mcc': 'str', '_mnc': 'str'}
    attribute_map = {'_mcc': 'mcc', '_mnc': 'mnc'}
    def __init__(self, mcc:str, mnc:str):  # noqa: E501
        self._mcc = None
        self.mcc = mcc
        self._mnc = None
        self.mnc = mnc
    @property
    def mcc(self):
        return self._mcc
    @mcc.setter
    def kpi_nmccame(self, mcc):
        self._mcc = mcc
    @property
    def mnc(self):
        return self._mnc
    @mnc.setter
    def kpi_nmccame(self, mnc):
        self._mnc = mnc
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,value))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(Plmn, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, Plmn):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class QosKpi(object):
    swagger_types = {'_kpi_name': 'str', '_kpi_value': 'str', '_confidence': 'str'}
    attribute_map = {'_kpi_name': 'kpiName', '_kpi_value': 'kpiValue', '_confidence': 'Confidence'}
    def __init__(self, kpi_name:str, kpi_value:str, confidence=None):  # noqa: E501
        self._kpi_name = None
        self._kpi_value = None
        self._confidence = None
        self.kpi_name = kpi_name
        self.kpi_value = kpi_value
        if confidence is not None:
            self.confidences = confidence
    @property
    def kpi_name(self):
        return self._kpi_name
    @kpi_name.setter
    def kpi_name(self, kpi_name):
        self._kpi_name = kpi_name
    @property
    def kpi_value(self):
        return self._kpi_value
    @kpi_value.setter
    def kpi_value(self, kpi_value):
        self._kpi_value = kpi_value
    @property
    def confidence(self):
        return self._confidence
    @confidence.setter
    def confidence(self, confidence):
        self._confidence = confidence
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,value))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(QosKpi, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, QosKpi):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class Stream(object):
    swagger_types = {'_stream_id': 'str', '_qos_kpi': 'list[QosKpi]'}
    attribute_map = {'_stream_id': 'streamId', '_qos_kpi': 'qosKpi'}
    def __init__(self, stream_id:str, qos_kpi:list):  # noqa: E501
        self._stream_id = None
        self._qos_kpi = None
        self.stream_id = stream_id
        self.qos_kpi = qos_kpi
    @property
    def stream_id(self):
        return self._stream_id
    @stream_id.setter
    def stream_id(self, stream_id):
        self._stream_id = stream_id
    @property
    def qos_kpi(self):
        return self._qos_kpi
    @qos_kpi.setter
    def qos_kpi(self, qos_kpi):
        self._qos_kpi = qos_kpi
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(
                    lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,
                    value
                ))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(Stream, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, Stream):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class Qos(object):
    swagger_types = {'_stream': 'list[Stream]'}
    attribute_map = {'_stream': 'stream'}
    def __init__(self, stream:list):  # noqa: E501
        self._stream = None
        self.stream = stream
    @property
    def stream(self):
        return self._stream
    @stream.setter
    def stream(self, stream):
        self._stream = stream
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(
                    lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,
                    value
                ))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(Qos, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, Qos):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class PredictedQos(object):
    swagger_types = {'_location_granularity': 'str', '_notice_period': 'TimeStamp', '_prediction_area': 'PredictionArea', '_predictionTarget': 'str', '_qos': 'Qos', '_routes': 'list[Routes]', '_time_granularity': 'TimeStamp'}
    attribute_map = {'_location_granularity': 'locationGranularity', '_notice_period': 'noticePeriod', '_prediction_area': 'predictionArea', '_prediction_target': 'predictionTarget', '_qos': 'qos', '_routes': 'routes', '_time_granularity': 'timeGranularity'}
    def __init__(self, prediction_target:str, location_granularity:str, notice_period=None, time_granularity=None, prediction_area=None, routes=None, qos=None):  # noqa: E501
        self._prediction_target = None
        self._time_granularity = None
        self._ = None
        self._notice_period = None
        self._prediction_area = None
        self._routes = None
        self._qos = Nonelocation_granularity
        self._prediction_target = prediction_target
        if time_ranularity is not None:
            self.time_granularity = time_granularityg
        self.location_granularity = location_granularity
        if notice_period is not None:
            self.notice_period = notice_period
        if prediction_area is not None:
            self.prediction_area = prediction_area
        if route is not None:
            self.routes = routes
        if qos is not None:
            self.qos = qos
    @property
    def prediction_target(self):
        return self._prediction_target
    @prediction_target.setter
    def prediction_target(self, prediction_target):
        self._prediction_target = prediction_target
    @property
    def time_granularity(self):
        return self._time_granularity
    @time_granularity.setter
    def time_granularity(self, time_granularity):
        self._time_granularity = time_granularity
    @property
    def location_granularity(self):
        return self._location_granularity
    @location_granularity.setter
    def location_granularity(self, location_granularity):
        self._location_granularity = location_granularity
    @property
    def notice_period(self):
        return self._notice_period
    @notice_period.setter
    def notice_period(self, notice_period):
        self._notice_period = notice_period
    @property
    def prediction_area(self):
        return self._prediction_area
    @prediction_area.setter
    def prediction_area(self, prediction_area):
        self._prediction_area = prediction_area
    @property
    def routes(self):
        return self._routes
    @routes.setter
    def routes(self, routes):
        self._routes = routes
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(
                    lambda x: x.to_dict() if hasattr(x, 'to_dict') else x,
                    value
                ))
            elif hasattr(value, 'to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], 'to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(PredictedQos, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, PredictedQos):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other


Here is the V2X Prediscted QoS:

In [83]:
def get_qos_prediction(sandbox_name: str) -> int:
    global MEC_PLTF, logger

    logger.debug('>>> get_qos_prediction: latitude: ' + sandbox_name)
    try:
        url = '/{sandbox_name}/{mec_pltf}/vis/v2//provide_predicted_qos'
        logger.debug('send_uu_unicast_provisioning_info: url: ' + url)
        path_params = {}
        path_params['sandbox_name'] = sandbox_name
        path_params['mec_pltf'] = MEC_PLTF
        # HTTP header `Accept`
        header_params['Accept'] = 'application/json'  # noqa: E501
        # HTTP header `Content-Type`
        header_params['Content-Type'] = 'application/json'  # noqa: E501
        # Body request
        loc1 = LocationInfo(LocationInfoGeoArea(latitude=43.729416, longitude=7.414853))
        loc2 = LocationInfo(LocationInfoGeoArea(latitude=43.732456, longitude=7.418417))
        routeInfo1 = RoutesInfo(loc1, TimeStamp(nanoSeconds=0, seconds=1653295620))
        routeInfo2 = RoutesInfo(loc2, TimeStamp(nanoSeconds=0, seconds=1653299220))
        routes = [routeInfo1, routeInfo2]
        predictedQos = PredictedQos(prediction_target="SINGLE_UE_PREDICTION", location_granularity="30", routes=routes)
        result = service_api.call_api(url, 'GET', header_params=header_params, path_params=path_params, body=predictedQos, async_req=False)
        return result
    except ApiException as e:
        logger.error('Exception when calling call_api: %s\n' % e)
    return None
    # End of function send_uu_unicast_provisioning_info

Grouping all together provides the process_main funtion.. The sequence is the following:
- Mec application setup
- V2X QoS request
- Mec application termination

The expected response should be:
- RSRP: 55
- RSRQ: 13

In [82]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Mec application setup
        - V2X QoS request
        - Mec application termination
    """ 
    global logger

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Setup the MEC application
    (sandbox_name, app_inst_id, sub_id) = mec_app_setup()

    # QoS Prediction
    result = get_qos_prediction(sandbox_name)
    if result is None:
        logger.error('Failed to get UU unicast provisioning information')
    else:
        logger.info('UU unicast provisioning information: ', str(result))
    
    # Delete the V2X message subscritpion
    delete_mec_subscription(v2x_resource)

    # Terminate the MEC application
    mec_app_termination(sandbox_name, app_inst_id, sub_id)

    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


2024-10-04 11:41:34,129 - __main__ - DEBUG - Starting at 20241004-114134
2024-10-04 11:41:34,129 - __main__ - DEBUG - Starting at 20241004-114134
2024-10-04 11:41:34,134 - __main__ - DEBUG - 	 pwd= /home/yann/dev/jupyter/Sandbox/mecapp
2024-10-04 11:41:34,134 - __main__ - DEBUG - 	 pwd= /home/yann/dev/jupyter/Sandbox/mecapp
2024-10-04 11:41:34,163 - __main__ - DEBUG - >>> process_login
2024-10-04 11:41:34,163 - __main__ - DEBUG - >>> process_login
2024-10-04 11:41:34,194 DEBUG Resetting dropped connection: mec-platform2.etsi.org
2024-10-04 11:41:34,373 DEBUG https://mec-platform2.etsi.org:443 "POST /sandbox-api/v1/login?provider=Jupyter2024 HTTP/1.1" 201 48
2024-10-04 11:41:34,375 DEBUG response body: b'{"user_code":"sbxj1uzhkb","verification_uri":""}'
2024-10-04 11:41:34,380 - __main__ - DEBUG - process_login (step1): oauth: {'user_code': 'sbxj1uzhkb', 'verification_uri': ''}
2024-10-04 11:41:34,380 - __main__ - DEBUG - process_login (step1): oauth: {'user_code': 'sbxj1uzhkb', 'verifi

send: b'POST /sandbox-api/v1/login?provider=Jupyter2024 HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 2\r\nAccept: application/json\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{}'
reply: 'HTTP/1.1 201 Created\r\n'
header: Date: Fri, 04 Oct 2024 09:41:34 GMT
header: Content-Type: application/json; charset=UTF-8
header: Content-Length: 48
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


2024-10-04 11:41:37,424 DEBUG https://mec-platform2.etsi.org:443 "GET /sandbox-api/v1/namespace?user_code=sbxj1uzhkb HTTP/1.1" 200 29
2024-10-04 11:41:37,427 DEBUG response body: b'{"sandbox_name":"sbxj1uzhkb"}'
2024-10-04 11:41:37,431 - __main__ - DEBUG - process_login (step2): result: {'sandbox_name': 'sbxj1uzhkb'}
2024-10-04 11:41:37,431 - __main__ - DEBUG - process_login (step2): result: {'sandbox_name': 'sbxj1uzhkb'}


send: b'GET /sandbox-api/v1/namespace?user_code=sbxj1uzhkb HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nAccept: application/json\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Date: Fri, 04 Oct 2024 09:41:37 GMT
header: Content-Type: application/json; charset=UTF-8
header: Content-Length: 29
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


2024-10-04 11:41:43,441 - __main__ - DEBUG - >>> get_network_scenarios: sandbox=sbxj1uzhkb
2024-10-04 11:41:43,441 - __main__ - DEBUG - >>> get_network_scenarios: sandbox=sbxj1uzhkb
2024-10-04 11:41:43,448 DEBUG Resetting dropped connection: mec-platform2.etsi.org
2024-10-04 11:41:43,656 DEBUG https://mec-platform2.etsi.org:443 "GET /sandbox-api/v1/sandboxNetworkScenarios?sandbox_name=sbxj1uzhkb HTTP/1.1" 200 157
2024-10-04 11:41:43,659 DEBUG response body: b'[{"id":"4g-5g-macro-v2x"},{"id":"4g-5g-wifi-macro"},{"id":"4g-macro"},{"id":"4g-wifi-macro"},{"id":"dual-mep-4g-5g-wifi-macro"},{"id":"dual-mep-short-path"}]'
2024-10-04 11:41:43,663 - __main__ - DEBUG - get_network_scenarios: result: [{'id': '4g-5g-macro-v2x'}, {'id': '4g-5g-wifi-macro'}, {'id': '4g-macro'}, {'id': '4g-wifi-macro'}, {'id': 'dual-mep-4g-5g-wifi-macro'}, {'id': 'dual-mep-short-path'}]
2024-10-04 11:41:43,663 - __main__ - DEBUG - get_network_scenarios: result: [{'id': '4g-5g-macro-v2x'}, {'id': '4g-5g-wifi-macro'}, 

...

send: b'POST /sandbox-api/v1/sandboxAppInstances/sbxj1uzhkb HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 107\r\nAccept: application/json\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{"id": "9fd5e0c9-c00c-4b7c-845b-ac91056d0482", "name": "JupyterMecApp", "nodeName": "mep1", "type": "USER"}'
reply: 'HTTP/1.1 201 Created\r\n'
header: Date: Fri, 04 Oct 2024 09:42:01 GMT
header: Content-Type: application/json; charset=UTF-8
header: Content-Length: 100
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains


2024-10-04 11:42:07,950 - __main__ - DEBUG - >>> send_ready_confirmation: 9fd5e0c9-c00c-4b7c-845b-ac91056d0482
2024-10-04 11:42:07,950 - __main__ - DEBUG - >>> send_ready_confirmation: 9fd5e0c9-c00c-4b7c-845b-ac91056d0482
2024-10-04 11:42:07,954 - __main__ - DEBUG - send_ready_confirmation: url: /{sandbox_name}/{mec_pltf}/mec_app_support/v2/applications/{app_inst_id}/confirm_ready
2024-10-04 11:42:07,954 - __main__ - DEBUG - send_ready_confirmation: url: /{sandbox_name}/{mec_pltf}/mec_app_support/v2/applications/{app_inst_id}/confirm_ready
2024-10-04 11:42:07,966 DEBUG Starting new HTTPS connection (1): mec-platform2.etsi.org:443
2024-10-04 11:42:08,099 DEBUG https://mec-platform2.etsi.org:443 "POST /sbxj1uzhkb/mep1/mec_app_support/v2/applications/9fd5e0c9-c00c-4b7c-845b-ac91056d0482/confirm_ready HTTP/1.1" 204 0
2024-10-04 11:42:08,099 DEBUG response body: b''
2024-10-04 11:42:08,100 - __main__ - DEBUG - >>> send_subscribe_termination: 9fd5e0c9-c00c-4b7c-845b-ac91056d0482
2024-10-04 1

send: b'POST /sbxj1uzhkb/mep1/mec_app_support/v2/applications/9fd5e0c9-c00c-4b7c-845b-ac91056d0482/confirm_ready HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 23\r\nAccept: application/json\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{"indication": "READY"}'
reply: 'HTTP/1.1 204 No Content\r\n'
header: Date: Fri, 04 Oct 2024 09:42:08 GMT
header: Content-Type: application/json; charset=UTF-8
header: Connection: keep-alive
header: Strict-Transport-Security: max-age=15724800; includeSubDomains
send: b'POST /sbxj1uzhkb/mep1/mec_app_support/v2/applications/9fd5e0c9-c00c-4b7c-845b-ac91056d0482/subscriptions HTTP/1.1\r\nHost: mec-platform2.etsi.org\r\nAccept-Encoding: identity\r\nContent-Length: 192\r\nAccept: application/json\r\nContent-Type: application/json\r\nUser-Agent: Swagger-Codegen/1.0.0/python\r\n\r\n'
send: b'{"subscriptionType": "AppTerminationNotificationSubscription", "callbackReference

2024-10-04 11:42:08,165 - __main__ - DEBUG - >>> extract_sub_id: resource_url: https://mec-platform2.etsi.org/sbxj1uzhkb/mep1/mec_app_support/v2/applications/9fd5e0c9-c00c-4b7c-845b-ac91056d0482/subscriptions/sub-VICy0s72InscM1yP
2024-10-04 11:42:08,165 - __main__ - DEBUG - >>> extract_sub_id: resource_url: https://mec-platform2.etsi.org/sbxj1uzhkb/mep1/mec_app_support/v2/applications/9fd5e0c9-c00c-4b7c-845b-ac91056d0482/subscriptions/sub-VICy0s72InscM1yP


TypeError: get_qos_prediction() missing 2 required positional arguments: 'latitude' and 'longitude'

## Our third MEC application: how to create a new MEC Services

<b>The cells below are under develpment</b>

The purpose of this MEC Service application is to provide a custom MEC service that can be use by other MEC applications. For the purpose of this tutorial, our MEC service is simulating some complex calculation based on a set of data provided by the MEC use.   
We will use a second MEC application to exploit the features of our new MEC services.

In this clause, we use the following functionalities provided by MEC-011:
- Register a new service
- Retrieve the list of the MEC services exposed by the MEC platform
- Check that our new MEC service is present in the list
- Delete a created service

<b>Note:</b> We will use a second MEC application to exploit the features of our new MEC services.


### Bases of the creation of a MEC service

From the user perspective, a MEC service provides a set of endpoints which describe the interface of the MEC service (see [HTTP REST APIs 
concepts](https://blog.postman.com/rest-api-examples/)). These endpoints come usually with a set of data structures used by the one or more endpoints.

Our service is really basic: it provide one endpoint:
- GET /statistic/v1/quantity: it computes statistical quantities of a set of data (such as average, max, min, standard deviation)

The body of this GET method is a list of datas:
```json
{"time":20180124,"data1":"[1516752000,11590.6,11616.9,11590.4,11616.9,0.25202387,1516752060,11622.4,11651.7,11622.4,11644.6,1.03977764]"}
```

The response body is the list of statistical quantities:
```json
{"time":20180124,"avg": 0.0,"max": 0.0,"min": 0.0,"stddev": 0.0 }
```


# Annexes

## Annex A: How to use an existing MEC sandbox instance

This case is used when the MEC Sandbox API is not used. The procedure is the following:
- Log to the MEC Sandbox using a WEB browser
- Select a network scenario
- Create a new application instance

When it is done, the newly created application instance is used by your application when required. This application instance is usually passed to your application in the command line or using a configuration file


### Bibliography

1. ETSI GS MEC 002 (V2.2.1) (01-2022): "Multi-access Edge Computing (MEC); Phase 2: Use Cases and Requirements".
2. ETSI GS MEC 010-1 (V1.1.1) (10-2017): "Mobile Edge Computing (MEC); Mobile Edge Management; Part 1: System, host and platform management".
3. ETSI GS MEC 010-2 (V2.2.1) (02-2022): "Multi-access Edge Computing (MEC); MEC Management; Part 2: Application lifecycle, rules and requirements management".
4. ETSI GS MEC 011 (V3.1.1) (09-2022): "Multi-access Edge Computing (MEC); Edge Platform Application Enablement".
5. ETSI GS MEC 012 (V2.2.1) (02-2022): "Multi-access Edge Computing (MEC); Radio Network Information API".
6. ETSI GS MEC 013 (V2.2.1) (01-2022): "Multi-access Edge Computing (MEC); Location API".
7. ETSI GS MEC 014 (V2.1.1) (03-2021): "Multi-access Edge Computing (MEC); UE Identity API".
8. ETSI GS MEC 015 (V2.1.1) (06-2020): "Multi-Access Edge Computing (MEC); Traffic Management APIs".
9. ETSI GS MEC 016 (V2.2.1) (04-2020): "Multi-access Edge Computing (MEC); Device application interface".
10. ETSI GS MEC 021 (V2.2.1) (02-2022): "Multi-access Edge Computing (MEC); Application Mobility Service API".
11. ETSI GS MEC 028 (V2.3.1) (07-2022): "Multi-access Edge Computing (MEC); WLAN Access Information API".
12. ETSI GS MEC 029 (V2.2.1) (01-2022): "Multi-access Edge Computing (MEC); Fixed Access Information API".
13. ETSI GS MEC 030 (V3.2.1) (05-2022): "Multi-access Edge Computing (MEC); V2X Information Service API".
14. ETSI GR MEC-DEC 025 (V2.1.1) (06-2019): "Multi-access Edge Computing (MEC); MEC Testing Framework".
15. ETSI GR MEC 001 (V3.1.1) (01-2022): "Multi-access Edge Computing (MEC); Terminology".
16. ETSI GR MEC 003 (V3.1.1): Multi-access Edge Computing (MEC); 
Framework and Reference Architecture
17. [The Wiki MEC web site](https://www.etsi.org/technologies/multi-access-edge-computing)
